# **Import all required libraries**

In [1]:
import pickle
import gzip
import os
from tensorflow import keras
import tensorflow as tf
from tensorflow.keras import mixed_precision
# import tensorflow_addons as tfa
# import keras_tuner
import cv2
import numpy as np
import re
import os
import torch
from tqdm.notebook import tqdm
from tensorflow.keras.applications import imagenet_utils
from tensorflow.keras.applications.efficientnet import EfficientNetB7, EfficientNetB0 
from tensorflow.keras.layers import GlobalAveragePooling2D
from tensorflow.keras.models import Model
from tensorflow.keras.applications.efficientnet import preprocess_input
from tensorflow.keras import mixed_precision
from openpyxl import Workbook, load_workbook
import platform
from progress.bar import Bar
import tqdm
import multiprocessing
import concurrent.futures

2023-12-24 22:00:49.895733: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-12-24 22:00:51.850142: I tensorflow/c/logging.cc:34] Successfully opened dynamic library libdirectml.d6f03b303ac3c4f2eeb8ca631688c9757b361310.so
2023-12-24 22:00:51.850214: I tensorflow/c/logging.cc:34] Successfully opened dynamic library libdxcore.so
2023-12-24 22:00:51.861196: I tensorflow/c/logging.cc:34] Successfully opened dynamic library libd3d12.so
2023-12-24 22:00:53.381045: I tensorflow/c/logging.cc:34] DirectML device enumeration: found 1 compatible adapters.


# **Enable fp16**

In [2]:
# tf.config.list_physical_devices('GPU')
# tf.keras.backend.clear_session()
# tf.config.run_functions_eagerly(True)

In [3]:
# mixed_precision.set_global_policy('mixed_float16')

# **Mention the destination of the files to access:**

In [4]:

# validation
vw_dest = "Dataset/excels/ISH_News_Sports final VAL.xlsx"
vo_dest = "Dataset/Pickles/excel_data.dev"
vf_dest = "Dataset/Final folder for frames"

# test
tw_dest = "Dataset/excels/ISH_News_Sports final TEST.xlsx"
to_dest = "Dataset/Pickles/excel_data.test"
tf_dest = "Dataset/Final folder for frames"

# train
w_dest = "Dataset/excels/ISH_News_Sports final TRAIN.xlsx"
o_dest = "Dataset/Pickles/excel_data.train"
f_dest = "Dataset/Final folder for frames"

In [5]:
def cls():
    system = platform.system()
    if system == 'Windows':
        os.system('cls')
    elif system == 'Linux':
        os.system('clear')
    elif system == 'MacOS':
        os.system('clear')

# **Initialise the CNN model here:**

In [6]:
base_model = EfficientNetB7(weights='imagenet', include_top=False)
x = base_model.output
x = GlobalAveragePooling2D()(x)
feature_extractor = Model(inputs=base_model.input, outputs=x)

2023-12-24 22:00:55.740426: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-12-24 22:00:55.743162: I tensorflow/c/logging.cc:34] DirectML: creating device on adapter 0 (NVIDIA GeForce RTX 3090)
2023-12-24 22:00:55.883558: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:306] Could not identify NUMA node of platform GPU ID 0, defaulting to 0. Your kernel may not have been built with NUMA support.
2023-12-24 22:00:55.883602: W tensorflow/core/common_runtime/pluggable_device/pluggable_device_bfc_allocator.cc:28] Overriding allow_growth setting because force_memory_growth was requested by the device.
2023-12-24 22:00:55.883625: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_f

# **Function for extraction of features:**

In [7]:

def get_features(filename, destination):
    input_string = filename
    pattern = r'\d+'
    match = re.search(pattern, input_string)
    features_listofList=[]
    if match:
        first_match = match.group()
        # print(first_match)
        # Get file path name
        input_folder = os.getcwd()+"/"+destination+"/"+first_match+"/"+input_string
        try:
            file_paths_frames = [file for file in sorted(os.listdir(input_folder)) if file.endswith(".jpg")]

            # base_model needs to be initialised first
            # x = base_model.output
            # x = GlobalAveragePooling2D()(x)
            # feature_extractor = Model(inputs=base_model.input, outputs=x)
    
            
            for indx, frame_file in enumerate(file_paths_frames):
                # Get the file
                frame_filename =  input_folder+"/" + frame_file
                print("frame_filename============", frame_filename,"\n")
                image = cv2.imread(frame_filename)
                
                #Image processing part
        
                # Define the coordinates of the ROI (top-left and bottom-right)
                x1, y1 = 535, 0  # Top-left corner of ROI
                x2, y2 = 1385, 1080  # Bottom-right corner of ROI
                #210*260
                # Crop the image to the specified ROI
                image = image[y1:y2, x1:x2]
                image = cv2.resize(image, (224, 224))  # Resize to the input size of MobileNet

                # Preprocess the image
                image = preprocess_input(image)
        
                # Expand dimensions to match the expected input shape (batch size of 1)
                image = np.expand_dims(image, axis=0)
                
                # Extract spatial embedding
                spatial_embedding = feature_extractor.predict(image)[0]
                
                features_listofList.append(spatial_embedding)
        except:
            print("The file is missing in the frames dataset\n")
    else:
        print("No match found.")
        return None

    # after this, the video must be in the form of features
    return torch.tensor(np.array(features_listofList))
    #return torch.tensor(features_listofList)

# **Function to create the pickle file:**

In [8]:
def create_pickle(workbook_dest, output_dest, frame_dest):
    # Load the excel file
    workbook = load_workbook(workbook_dest)
    sheet = workbook.active

    # Extract data from the Excel file
    excel_data = []
    for row in sheet.iter_rows(values_only=True):
        excel_data.append(row)
        # print(excel_data,"\n")
        # print(excel_data)list_of_inputs = []
    
    # Get the features
    list_of_inputs = []
    
    for tmp in excel_data:
        features = get_features(str(tmp[0]),frame_dest)
        if(features!= None):
            data_dict = {}
            data_dict['name'] = tmp[0]
            data_dict['signer'] = tmp[1]
            data_dict['gloss'] = tmp[2]
            data_dict['text'] = tmp[3]
            data_dict['sign'] = features + 1e-7
            #print(data_dict)
            #input()
            list_of_inputs.append(data_dict)

    # print("\nlist_of_input:\n")
    # print(list_of_inputs)
    with gzip.open(os.getcwd() + "/" + output_dest,'wb') as f:
        pickle.dump(list_of_inputs,f)

# **Call for training:**

In [9]:
# Testing pickle
create_pickle(tw_dest, to_dest, tf_dest)

print("Testing pickle Creation Successful")

In [ ]:
# Training pickle
create_pickle(w_dest, o_dest, f_dest)

print("Training pickle Creation Successful")

frame_filename============ /home/rahu_g/islt_directml/Pre-Processing/Pickle maker/Dataset/Final folder for frames/100/100_2.00/frame_0067.jpg 



2023-12-24 22:01:03.062341: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:114] Plugin optimizer for device_type GPU is enabled.
2023-12-24 22:01:04.039036: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:306] Could not identify NUMA node of platform GPU ID 0, defaulting to 0. Your kernel may not have been built with NUMA support.
2023-12-24 22:01:04.039108: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:272] Created TensorFlow device (/job:localhost/replica:0/task:0/device:GPU:0 with 52200 MB memory) -> physical PluggableDevice (device: 0, name: DML, pci bus id: <undefined>)
2023-12-24 22:01:04.040959: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:306] Could not identify NUMA node of platform GPU ID 0, defaulting to 0. Your kernel may not have been built with NUMA support.
2023-12-24 22:01:04.041003: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_f

1/1 [==============================] - 8s 8s/step
frame_filename============ /home/rahu_g/islt_directml/Pre-Processing/Pickle maker/Dataset/Final folder for frames/100/100_2.00/frame_0069.jpg 

1/1 [==============================] - 0s 41ms/step
frame_filename============ /home/rahu_g/islt_directml/Pre-Processing/Pickle maker/Dataset/Final folder for frames/100/100_2.00/frame_0071.jpg 

1/1 [==============================] - 0s 31ms/step
frame_filename============ /home/rahu_g/islt_directml/Pre-Processing/Pickle maker/Dataset/Final folder for frames/100/100_2.00/frame_0073.jpg 

1/1 [==============================] - 0s 32ms/step
frame_filename============ /home/rahu_g/islt_directml/Pre-Processing/Pickle maker/Dataset/Final folder for frames/100/100_2.00/frame_0075.jpg 

1/1 [==============================] - 0s 32ms/step
frame_filename============ /home/rahu_g/islt_directml/Pre-Processing/Pickle maker/Dataset/Final folder for frames/100/100_2.00/frame_0077.jpg 

1/1 [=================

IOPub message rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_msg_rate_limit`.

Current values:
ServerApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
ServerApp.rate_limit_window=3.0 (secs)



1/1 [==============================] - 0s 37ms/step
frame_filename============ /home/rahu_g/islt_directml/Pre-Processing/Pickle maker/Dataset/Final folder for frames/103/103_79.00/frame_2059.jpg 

1/1 [==============================] - 0s 39ms/step
frame_filename============ /home/rahu_g/islt_directml/Pre-Processing/Pickle maker/Dataset/Final folder for frames/103/103_79.00/frame_2061.jpg 

1/1 [==============================] - 0s 37ms/step
frame_filename============ /home/rahu_g/islt_directml/Pre-Processing/Pickle maker/Dataset/Final folder for frames/103/103_79.00/frame_2063.jpg 

1/1 [==============================] - 0s 36ms/step
frame_filename============ /home/rahu_g/islt_directml/Pre-Processing/Pickle maker/Dataset/Final folder for frames/103/103_79.00/frame_2065.jpg 

1/1 [==============================] - 0s 37ms/step
frame_filename============ /home/rahu_g/islt_directml/Pre-Processing/Pickle maker/Dataset/Final folder for frames/103/103_79.00/frame_2067.jpg 

1/1 [==========

...

frame_filename============ /home/rahu_g/islt_directml/Pre-Processing/Pickle maker/Dataset/Final folder for frames/123/123_84.00/frame_2455.jpg 

1/1 [==============================] - 0s 40ms/step
frame_filename============ /home/rahu_g/islt_directml/Pre-Processing/Pickle maker/Dataset/Final folder for frames/123/123_84.00/frame_2457.jpg 

1/1 [==============================] - 0s 37ms/step
frame_filename============ /home/rahu_g/islt_directml/Pre-Processing/Pickle maker/Dataset/Final folder for frames/123/123_84.00/frame_2459.jpg 

1/1 [==============================] - 0s 40ms/step
frame_filename============ /home/rahu_g/islt_directml/Pre-Processing/Pickle maker/Dataset/Final folder for frames/123/123_84.00/frame_2461.jpg 

1/1 [==============================] - 0s 38ms/step
frame_filename============ /home/rahu_g/islt_directml/Pre-Processing/Pickle maker/Dataset/Final folder for frames/123/123_84.00/frame_2463.jpg 

1/1 [==============================] - 0s 37ms/step
frame_filename=

IOPub message rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_msg_rate_limit`.

Current values:
ServerApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
ServerApp.rate_limit_window=3.0 (secs)



frame_filename============ /home/rahu_g/islt_directml/Pre-Processing/Pickle maker/Dataset/Final folder for frames/127/127_180.00/frame_4805.jpg 

1/1 [==============================] - 0s 35ms/step
frame_filename============ /home/rahu_g/islt_directml/Pre-Processing/Pickle maker/Dataset/Final folder for frames/127/127_180.00/frame_4807.jpg 

1/1 [==============================] - 0s 33ms/step
frame_filename============ /home/rahu_g/islt_directml/Pre-Processing/Pickle maker/Dataset/Final folder for frames/127/127_180.00/frame_4809.jpg 

1/1 [==============================] - 0s 33ms/step
frame_filename============ /home/rahu_g/islt_directml/Pre-Processing/Pickle maker/Dataset/Final folder for frames/127/127_180.00/frame_4811.jpg 

1/1 [==============================] - 0s 33ms/step
frame_filename============ /home/rahu_g/islt_directml/Pre-Processing/Pickle maker/Dataset/Final folder for frames/127/127_180.00/frame_4813.jpg 

1/1 [==============================] - 0s 36ms/step
frame_file

IOPub message rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_msg_rate_limit`.

Current values:
ServerApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
ServerApp.rate_limit_window=3.0 (secs)



frame_filename============ /home/rahu_g/islt_directml/Pre-Processing/Pickle maker/Dataset/Final folder for frames/131/131_29.00/frame_1085.jpg 

1/1 [==============================] - 0s 35ms/step
frame_filename============ /home/rahu_g/islt_directml/Pre-Processing/Pickle maker/Dataset/Final folder for frames/131/131_29.00/frame_1087.jpg 

1/1 [==============================] - 0s 36ms/step
frame_filename============ /home/rahu_g/islt_directml/Pre-Processing/Pickle maker/Dataset/Final folder for frames/131/131_29.00/frame_1089.jpg 

1/1 [==============================] - 0s 36ms/step
frame_filename============ /home/rahu_g/islt_directml/Pre-Processing/Pickle maker/Dataset/Final folder for frames/131/131_29.00/frame_1091.jpg 

1/1 [==============================] - 0s 41ms/step
frame_filename============ /home/rahu_g/islt_directml/Pre-Processing/Pickle maker/Dataset/Final folder for frames/131/131_29.00/frame_1093.jpg 

1/1 [==============================] - 0s 36ms/step
frame_filename=

In [ ]:
# Validation pickle
create_pickle(vw_dest, vo_dest, vf_dest)

print("Validation/dev pickle Creation Successful")